In [1]:
import gym
import numpy as np
rm='Pong-v0'

In [2]:
%matplotlib inline
from matplotlib import animation
import matplotlib.pyplot as plt
from IPython.display import display, HTML

def display_frames_as_gif(frames):
    plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 144)
    patch = plt.imshow(frames[0])
    plt.axis('off')
    def animate(i):
        patch.set_data(frames[i])
    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=50)
    plt.close(anim._fig)
    display(HTML(anim.to_jshtml()))

In [3]:
from gym.wrappers import AtariPreprocessing
gym.new_step_api=True
env = gym.make(rm)
# model initialization
H = 200 # number of hidden layer neurons
D = 80 * 80 # input dimensionality: 80x80 grid
model = {}
model['W1'] = np.random.randn(H,D) / np.sqrt(D) # "Xavier" initialization
model['W2'] = np.random.randn(H) / np.sqrt(H)
# hyperparameters
batch_size = 10 # every how many episodes to do a param update?
learning_rate = 1e-3
gamma = 0.99 # discount factor for reward
decay_rate = 0.99 # decay factor for RMSProp leaky sum of grad^2
grad_buffer = { k : np.zeros_like(v) for k,v in model.items() } # update buffers that add up gradients over a batch
rmsprop_cache = { k : np.zeros_like(v) for k,v in model.items() } # rmsprop memory

def sigmoid(x): 
  return 1.0 / (1.0 + np.exp(-x)) # sigmoid "squashing" function to interval [0,1]

def prepro(I):
  I=np.asarray(I)
  I = I[35:195] # crop
  I = I[::2,::2,0] # downsample by factor of 2
  
  I[I == 144] = 0 # erase background (background type 1)
  
  I[I == 109] = 0 # erase background (background type 2)
  
  I[I != 0] = 1 # everything else (paddles, ball) just set to 1
  return I.astype(float).ravel()

def discount_rewards(r):
  discounted_r = np.zeros_like(r)
  running_add = 0
  for t in reversed(range(0, r.size)):
    if r[t] != 0: running_add = 0 # reset the sum, since this was a game boundary (pong specific!)
    running_add = running_add * gamma + r[t]
    discounted_r[t] = running_add
  return discounted_r

def policy_forward(x):
  h = np.dot(model['W1'], x)
  h[h<0] = 0 # ReLU nonlinearity
  logp = np.dot(model['W2'], h)
  p = sigmoid(logp)
  return p, h # return probability of taking action 2, and hidden state

def policy_backward(epx, eph, epdlogp):
  """ backward pass. (eph is array of intermediate hidden states) """
  dW2 = np.dot(eph.T, epdlogp).ravel()
  dh = np.outer(epdlogp, model['W2'])
  dh[eph <= 0] = 0 # backpro prelu
  dW1 = np.dot(dh.T, epx)
  return {'W1':dW1, 'W2':dW2}

def model_step(model, observation, prev_x):
  # preprocess the observation, set input to network to be difference image
  cur_x = prepro(observation)
  x = cur_x - prev_x if prev_x is not None else np.zeros(D)
  prev_x = cur_x
  
  # forward the policy network and sample an action from the returned probability
  aprob, _ = policy_forward(x)
  action = 2 if aprob >= 0.5 else 3 # roll the dice!
  
  return action, prev_x

def play_game(env, model):
  observation = env.reset()

  frames = []
  cumulated_reward = 0

  prev_x = None # used in computing the difference frame

  for t in range(1000):
      frames.append(env.render(mode = 'rgb_array'))
      action, prev_x = model_step(model, observation, prev_x)
      observation, reward, done, info = env.step(action)
      cumulated_reward += reward
      if done:
          print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
          break
  print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))
  env.close()
  display_frames_as_gif(frames)

def train_model(env, model, total_episodes = 100):
  hist = []
  observation = env.reset()

  prev_x = None # used in computing the difference frame
  xs,hs,dlogps,drs = [],[],[],[]
  running_reward = None
  reward_sum = 0
  episode_number = 0

  while True:
    # preprocess the observation, set input to network to be difference image
    cur_x = prepro(observation)
    x = cur_x - prev_x if prev_x is not None else np.zeros(D)
    prev_x = cur_x

    # forward the policy network and sample an action from the returned probability
    aprob, h = policy_forward(x)
    action = 2 if np.random.uniform() < aprob else 3 # roll the dice!

    # record various intermediates (needed later for backprop)
    xs.append(x) # observation
    hs.append(h) # hidden state
    y = 1 if action == 2 else 0 # a "fake label"
    dlogps.append(y - aprob) # grad that encourages the action that was taken to be taken (see http://cs231n.github.io/neural-networks-2/#losses if confused)

    # step the environment and get new measurements
    observation, reward, done, info = env.step(action)
    reward_sum += reward

    drs.append(reward) # record reward (has to be done after we call step() to get reward for previous action)

    if done: # an episode finished
      episode_number += 1

      # stack together all inputs, hidden states, action gradients, and rewards for this episode
      epx = np.vstack(xs)
      eph = np.vstack(hs)
      epdlogp = np.vstack(dlogps)
      epr = np.vstack(drs)
      xs,hs,dlogps,drs = [],[],[],[] # reset array memory

      # compute the discounted reward backwards through time
      discounted_epr = discount_rewards(epr)
      # standardize the rewards to be unit normal (helps control the gradient estimator variance)
      discounted_epr -= np.mean(discounted_epr)
      discounted_epr /= np.std(discounted_epr)

      epdlogp *= discounted_epr # modulate the gradient with advantage (PG magic happens right here.)
      grad = policy_backward(epx, eph, epdlogp)
      for k in model: grad_buffer[k] += grad[k] # accumulate grad over batch

      # perform rmsprop parameter update every batch_size episodes
      if episode_number % batch_size == 0:
        for k,v in model.items():
          g = grad_buffer[k] # gradient
          rmsprop_cache[k] = decay_rate * rmsprop_cache[k] + (1 - decay_rate) * g**2
          model[k] += learning_rate * g / (np.sqrt(rmsprop_cache[k]) + 1e-5)
          grad_buffer[k] = np.zeros_like(v) # reset batch gradient buffer

      # boring book-keeping
      running_reward = reward_sum if running_reward is None else running_reward * 0.99 + reward_sum * 0.01
      hist.append((episode_number, reward_sum, running_reward))
      print ('episode %f, reward total was %f. running mean: %f' % (episode_number, reward_sum, running_reward))
      reward_sum = 0
      observation = env.reset() # reset env
      prev_x = None
      if episode_number == total_episodes: 
        return hist

    # if reward != 0: # Pong has either +1 or -1 reward exactly when game ends.
    #   print('ep {}: game finished, reward: {}'.format(episode_number, reward) + ('' if reward == -1 else ' !!!!!!!!'))

c:\users\lenovo\appdata\local\programs\python\python38\lib\site-packages\gym\envs\registration.py:592: UserWarning: WARN: The environment Pong-v0 is out of date. You should consider upgrading to version `v4`.
  logger.warn(
c:\users\lenovo\appdata\local\programs\python\python38\lib\site-packages\gym\core.py:329: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
c:\users\lenovo\appdata\local\programs\python\python38\lib\site-packages\gym\wrappers\step_api_compatibility.py:39: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(


In [4]:
%time hist1 = train_model(env, model, total_episodes=6000)

c:\users\lenovo\appdata\local\programs\python\python38\lib\site-packages\gym\utils\passive_env_checker.py:227: DeprecationWarning: WARN: Core environment is written in old step API which returns one bool instead of two. It is recommended to rewrite the environment with new step API. 
  logger.deprecation(


episode 1.000000, reward total was -21.000000. running mean: -21.000000
episode 2.000000, reward total was -20.000000. running mean: -20.990000
episode 3.000000, reward total was -21.000000. running mean: -20.990100
episode 4.000000, reward total was -20.000000. running mean: -20.980199
episode 5.000000, reward total was -21.000000. running mean: -20.980397
episode 6.000000, reward total was -21.000000. running mean: -20.980593
episode 7.000000, reward total was -21.000000. running mean: -20.980787
episode 8.000000, reward total was -19.000000. running mean: -20.960979
episode 9.000000, reward total was -21.000000. running mean: -20.961369
episode 10.000000, reward total was -21.000000. running mean: -20.961756
episode 11.000000, reward total was -21.000000. running mean: -20.962138
episode 12.000000, reward total was -18.000000. running mean: -20.932517
episode 13.000000, reward total was -21.000000. running mean: -20.933192
episode 14.000000, reward total was -21.000000. running mean

episode 114.000000, reward total was -21.000000. running mean: -20.659457
episode 115.000000, reward total was -21.000000. running mean: -20.662863
episode 116.000000, reward total was -20.000000. running mean: -20.656234
episode 117.000000, reward total was -19.000000. running mean: -20.639672
episode 118.000000, reward total was -20.000000. running mean: -20.633275
episode 119.000000, reward total was -21.000000. running mean: -20.636942
episode 120.000000, reward total was -21.000000. running mean: -20.640573
episode 121.000000, reward total was -19.000000. running mean: -20.624167
episode 122.000000, reward total was -20.000000. running mean: -20.617925
episode 123.000000, reward total was -20.000000. running mean: -20.611746
episode 124.000000, reward total was -21.000000. running mean: -20.615629
episode 125.000000, reward total was -21.000000. running mean: -20.619472
episode 126.000000, reward total was -21.000000. running mean: -20.623278
episode 127.000000, reward total was -

episode 225.000000, reward total was -21.000000. running mean: -20.328372
episode 226.000000, reward total was -20.000000. running mean: -20.325088
episode 227.000000, reward total was -20.000000. running mean: -20.321837
episode 228.000000, reward total was -19.000000. running mean: -20.308619
episode 229.000000, reward total was -20.000000. running mean: -20.305533
episode 230.000000, reward total was -18.000000. running mean: -20.282477
episode 231.000000, reward total was -21.000000. running mean: -20.289653
episode 232.000000, reward total was -21.000000. running mean: -20.296756
episode 233.000000, reward total was -21.000000. running mean: -20.303789
episode 234.000000, reward total was -20.000000. running mean: -20.300751
episode 235.000000, reward total was -21.000000. running mean: -20.307743
episode 236.000000, reward total was -17.000000. running mean: -20.274666
episode 237.000000, reward total was -18.000000. running mean: -20.251919
episode 238.000000, reward total was -

episode 336.000000, reward total was -21.000000. running mean: -20.010991
episode 337.000000, reward total was -19.000000. running mean: -20.000881
episode 338.000000, reward total was -21.000000. running mean: -20.010872
episode 339.000000, reward total was -20.000000. running mean: -20.010763
episode 340.000000, reward total was -21.000000. running mean: -20.020656
episode 341.000000, reward total was -21.000000. running mean: -20.030449
episode 342.000000, reward total was -20.000000. running mean: -20.030145
episode 343.000000, reward total was -20.000000. running mean: -20.029843
episode 344.000000, reward total was -17.000000. running mean: -19.999545
episode 345.000000, reward total was -20.000000. running mean: -19.999549
episode 346.000000, reward total was -19.000000. running mean: -19.989554
episode 347.000000, reward total was -21.000000. running mean: -19.999658
episode 348.000000, reward total was -17.000000. running mean: -19.969662
episode 349.000000, reward total was -

...

episode 5525.000000, reward total was -12.000000. running mean: -8.978535
episode 5526.000000, reward total was -10.000000. running mean: -8.988750
episode 5527.000000, reward total was -13.000000. running mean: -9.028862
episode 5528.000000, reward total was -7.000000. running mean: -9.008574
episode 5529.000000, reward total was -13.000000. running mean: -9.048488
episode 5530.000000, reward total was -16.000000. running mean: -9.118003
episode 5531.000000, reward total was -13.000000. running mean: -9.156823
episode 5532.000000, reward total was -11.000000. running mean: -9.175255
episode 5533.000000, reward total was -13.000000. running mean: -9.213502
episode 5534.000000, reward total was -8.000000. running mean: -9.201367
episode 5535.000000, reward total was -16.000000. running mean: -9.269353
episode 5536.000000, reward total was -11.000000. running mean: -9.286660
episode 5537.000000, reward total was -7.000000. running mean: -9.263793
episode 5538.000000, reward total was -7.

episode 5637.000000, reward total was -7.000000. running mean: -9.527363
episode 5638.000000, reward total was -10.000000. running mean: -9.532090
episode 5639.000000, reward total was -6.000000. running mean: -9.496769
episode 5640.000000, reward total was -10.000000. running mean: -9.501801
episode 5641.000000, reward total was -7.000000. running mean: -9.476783
episode 5642.000000, reward total was -12.000000. running mean: -9.502015
episode 5643.000000, reward total was -7.000000. running mean: -9.476995
episode 5644.000000, reward total was -10.000000. running mean: -9.482225
episode 5645.000000, reward total was -8.000000. running mean: -9.467403
episode 5646.000000, reward total was -12.000000. running mean: -9.492729
episode 5647.000000, reward total was -14.000000. running mean: -9.537802
episode 5648.000000, reward total was -15.000000. running mean: -9.592424
episode 5649.000000, reward total was -13.000000. running mean: -9.626499
episode 5650.000000, reward total was -7.00

episode 5749.000000, reward total was -6.000000. running mean: -8.926039
episode 5750.000000, reward total was -12.000000. running mean: -8.956779
episode 5751.000000, reward total was -5.000000. running mean: -8.917211
episode 5752.000000, reward total was -6.000000. running mean: -8.888039
episode 5753.000000, reward total was -10.000000. running mean: -8.899159
episode 5754.000000, reward total was -12.000000. running mean: -8.930167
episode 5755.000000, reward total was -17.000000. running mean: -9.010865
episode 5756.000000, reward total was -5.000000. running mean: -8.970757
episode 5757.000000, reward total was -13.000000. running mean: -9.011049
episode 5758.000000, reward total was -9.000000. running mean: -9.010939
episode 5759.000000, reward total was -5.000000. running mean: -8.970829
episode 5760.000000, reward total was -13.000000. running mean: -9.011121
episode 5761.000000, reward total was -13.000000. running mean: -9.051010
episode 5762.000000, reward total was -11.00

episode 5861.000000, reward total was -10.000000. running mean: -8.742926
episode 5862.000000, reward total was -7.000000. running mean: -8.725497
episode 5863.000000, reward total was -15.000000. running mean: -8.788242
episode 5864.000000, reward total was -13.000000. running mean: -8.830360
episode 5865.000000, reward total was -14.000000. running mean: -8.882056
episode 5866.000000, reward total was -12.000000. running mean: -8.913235
episode 5867.000000, reward total was -10.000000. running mean: -8.924103
episode 5868.000000, reward total was -4.000000. running mean: -8.874862
episode 5869.000000, reward total was -13.000000. running mean: -8.916113
episode 5870.000000, reward total was -7.000000. running mean: -8.896952
episode 5871.000000, reward total was -11.000000. running mean: -8.917983
episode 5872.000000, reward total was -5.000000. running mean: -8.878803
episode 5873.000000, reward total was -14.000000. running mean: -8.930015
episode 5874.000000, reward total was -13.

episode 5973.000000, reward total was -12.000000. running mean: -8.967271
episode 5974.000000, reward total was -7.000000. running mean: -8.947599
episode 5975.000000, reward total was -7.000000. running mean: -8.928123
episode 5976.000000, reward total was -4.000000. running mean: -8.878841
episode 5977.000000, reward total was -7.000000. running mean: -8.860053
episode 5978.000000, reward total was -7.000000. running mean: -8.841452
episode 5979.000000, reward total was -7.000000. running mean: -8.823038
episode 5980.000000, reward total was -13.000000. running mean: -8.864808
episode 5981.000000, reward total was -9.000000. running mean: -8.866159
episode 5982.000000, reward total was -10.000000. running mean: -8.877498
episode 5983.000000, reward total was -12.000000. running mean: -8.908723
episode 5984.000000, reward total was -16.000000. running mean: -8.979636
episode 5985.000000, reward total was -9.000000. running mean: -8.979839
episode 5986.000000, reward total was -9.00000

In [5]:
play_game(env, model)

c:\users\lenovo\appdata\local\programs\python\python38\lib\site-packages\gym\core.py:51: DeprecationWarning: WARN: The argument mode in render method is deprecated; use render_mode during environment initialization instead.
See here for more information: https://www.gymlibrary.ml/content/api/
  deprecation(
c:\users\lenovo\appdata\local\programs\python\python38\lib\site-packages\gym\utils\passive_env_checker.py:297: UserWarning: WARN: No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps.
  logger.warn(


Episode finished without success, accumulated reward = -2.0
